In [1]:
import cupy as cp
import numpy as np
from time import perf_counter
import time
from pyqcu import define
from pyqcu import io
from pyqcu import qcu
import cupyx.scipy.sparse.linalg as csla
import scipy.linalg as sla

print('My rank is ', define.rank)


    @@@@@@######QCU NOTES START######@@@@@@@
    1. The libqcu.so was compiled when pyqcu setup in download_path/PyQCU/lib, please add this path to your LD_LIBRARY_PATH.
    2. The QCU(PyQCU) splite grid by x->y->z->t, lattice by x->y->z->t->p->d->c->c or x->y->z->t->c->s(->p) and x->y->z->t->c->s->c->s(->p).
    3. The QUDA(PyQUDA) splite grid by t->z->y->x, lattice by c->c->x->y->z->t->p->d or c->s->x->y->z->t(->p) and c->s->c->s->x->y->z->t(->p).
    4. The QCU input params in numpy array(dtype=np.int32), argv in  numpy array(dtype=np.float32 or float64) array, set_ptrs in numpy array(dtype=np.int64), other in cupy array(dtype=cp.complex64 or complex128).
    5. The smallest lattice size is (x=4,y=4,z=4,t=8) that QCU support.
    @@@@@@######QCU NOTES END######@@@@@@@
    
My rank is  0


In [2]:
params = np.array([0]*define._PARAMS_SIZE_, dtype=np.int32)
params[define._LAT_X_] = 32
params[define._LAT_Y_] = 32
params[define._LAT_Z_] = 32
params[define._LAT_T_] = 32
params[define._LAT_XYZT_] = 1048576
params[define._GRID_X_] = 1
params[define._GRID_Y_] = 1
params[define._GRID_Z_] = 1
params[define._GRID_T_] = 1
params[define._PARITY_] = 0
params[define._NODE_RANK_] = 0
params[define._NODE_SIZE_] = 1
params[define._DAGGER_] = 0
params[define._MAX_ITER_] = 200
params[define._DATA_TYPE_] = 0
params[define._SET_INDEX_] = 2
params[define._SET_PLAN_] = 0
argv = np.array([0.0]*define._ARGV_SIZE_, dtype=np.float32)
argv[define._MASS_] = 0.0
argv[define._TOL_] = 1e-6
print("Parameters:", params)
print("Arguments:", argv)
# give x, b, r, r_tilde, p, v, s, t
lat_t = params[define._LAT_T_]
lat_z = params[define._LAT_Z_]
lat_y = params[define._LAT_Y_]
lat_x = int(params[define._LAT_X_]/define._LAT_P_)
lat_d = define._LAT_D_
lat_s = define._LAT_S_
lat_p = define._LAT_P_
lat_c = define._LAT_C_
latt_shape = (lat_s, lat_c, lat_t, lat_z, lat_y, lat_x)
max_iter = params[define._MAX_ITER_]
tol = argv[define._TOL_]
n = params[define._LAT_XYZT_] * define._LAT_HALF_SC_
define._LAT_Ne_ = 24
k = define._LAT_Ne_
min_eigen_value = 0.0
max_eigen_value = 1.0
degree = 10

Parameters: [     32      32      32      32 1048576       1       1       1       1
       0       0       1       0     200       0       2       0]
Arguments: [0.e+00 1.e-06]


In [3]:
gauge_filename = f"quda_wilson-dslash-gauge_-{params[define._LAT_X_]}-{params[define._LAT_Y_]}-{params  [define._LAT_Z_]}-{params[define._LAT_T_]}-{params[define._LAT_XYZT_]}-{params[define._GRID_X_]}-{params[define._GRID_Y_]}-{params[define._GRID_Z_]}-{params[define._GRID_T_]}-{params[define._PARITY_]}-{params[define._NODE_RANK_]}-{params[define._NODE_SIZE_]}-{params[define._DAGGER_]}-f.bin"
print("Gauge filename:", gauge_filename)
gauge = cp.fromfile(gauge_filename, dtype=cp.complex64,
                    count=params[define._LAT_XYZT_]*define._LAT_DCC_)
gauge = io.gauge2ccdptzyx(gauge, params)
print("Gauge:", gauge)
print("Gauge data:", gauge.data)
print("Gauge shape:", gauge.shape)

Gauge filename: quda_wilson-dslash-gauge_-32-32-32-32-1048576-1-1-1-1-0-0-1-0-f.bin
U: [ 0.9888613 +0.02130369j  0.07348315-0.02076806j -0.09857995+0.07842391j
 -0.07511304-0.01086277j  0.9932049 -0.00666964j  0.04573338+0.07515373j
  0.10230845+0.07397576j -0.03536638+0.08011071j  0.9880291 -0.01380186j]
_U: [ 0.        +0.j          0.        +0.j          0.        +0.j
  0.        +0.j          0.        +0.j          0.        +0.j
  0.10230846+0.07397576j -0.03536638+0.08011071j  0.9880291 -0.01380186j]
Gauge: 37748736
Gauge: [[[[[[[[ 9.88861322e-01+2.13036854e-02j
         9.90962327e-01+5.69420774e-03j
         9.87317920e-01-1.84401460e-02j ...
         9.82378662e-01-1.55471310e-01j
         9.85994279e-01+8.39557722e-02j
         9.77860272e-01+1.58485785e-01j]
       [ 9.87088621e-01-4.39827666e-02j
         9.86678004e-01+7.97407404e-02j
         9.95163381e-01+4.71003056e-02j ...
         9.88952160e-01-4.90137562e-02j
         9.68354821e-01-9.38901827e-02j
         9.92

In [4]:
set_ptrs = np.array(params, dtype=np.int64)
print("Set pointers:", set_ptrs)
print("Set pointers data:", set_ptrs.data)
qcu.applyInitQcu(set_ptrs, params, argv)

Set pointers: [     32      32      32      32 1048576       1       1       1       1
       0       0       1       0     200       0       2       0]
Set pointers data: <memory at 0x7fb7501710c0>
gridDim.x               :4096
blockDim.x              :128
host_params[_LAT_X_]    :16
host_params[_LAT_Y_]    :32
host_params[_LAT_Z_]    :32
host_params[_LAT_T_]    :32
host_params[_LAT_XYZT_] :524288
host_params[_GRID_X_]   :1
host_params[_GRID_Y_]   :1
host_params[_GRID_Z_]   :1
host_params[_GRID_T_]   :1
host_params[_PARITY_]   :0
host_params[_NODE_RANK_]:0
host_params[_NODE_SIZE_]:1
host_params[_DAGGER_]   :0
host_params[_MAX_ITER_] :200
host_params[_SET_INDEX_]:2
host_params[_SET_PLAN_] :0
host_argv[_MASS_]       :0.000000e+00
host_argv[_TOL_]        :1.000000e-06
lat_2dim[_XY_]          :512
lat_2dim[_XZ_]          :512
lat_2dim[_XT_]          :512
lat_2dim[_YZ_]          :1024
lat_2dim[_YT_]          :1024
lat_2dim[_ZT_]          :1024
lat_3dim[_YZT_]         :32768
lat_3dim[_XZT_]

In [5]:
class EigenSolver:
    def __init__(self, n=n, k=k, degree=degree, max_iter=max_iter, tol=tol, min_eigen_value=min_eigen_value, max_eigen_value=max_eigen_value):
        self.n = n
        self.k = k
        self.degree = degree
        self.max_iter = max_iter
        self.tol = tol
        self.min_eigen_value = min_eigen_value
        self.max_eigen_value = max_eigen_value
        self.buffers = {
            'v': cp.zeros(n, dtype=cp.complex64),
            'w': cp.zeros(n, dtype=cp.complex64),
            'temp': cp.zeros(n, dtype=cp.complex64),
            'matvec_result': cp.zeros(n, dtype=cp.complex64),
            'projection': cp.zeros(n, dtype=cp.complex64)
        }
        self.memory_pool = cp.cuda.MemoryPool()
        cp.cuda.set_allocator(self.memory_pool.malloc)
        self.min_degree = 10
        self.max_degree = 100
        self.growth_factor = 1.5
        self.shrink_factor = 0.5

    def initialize_random_vector(self, v):
        v.real = cp.random.randn(self.n).astype(cp.float32)
        v.imag = cp.random.randn(self.n).astype(cp.float32)
        norm = cp.linalg.norm(v)
        if norm > 0:
            cp.divide(v, norm, out=v)
        return v

    def matvec(self, src):
        qcu.applyWilsonCgDslashQcu(
            self.buffers['matvec_result'], src, gauge, set_ptrs, params)
        return self.buffers['matvec_result']

    def estimate_spectral_range(self, num_samples=20):
        """Estimate spectral range using inverse iteration for smallest eigenvalue"""
        v = self.initialize_random_vector(self.buffers['temp'])
        # Inverse iteration for smallest eigenvalue
        w = v.copy()
        lambda_min = float('inf')
        # Simple inverse iteration with shift
        shift = self.min_eigen_value * 0.95  # Shift slightly below expected minimum
        for _ in range(num_samples):
            # Approximate (A - shift*I)^(-1) * w using a few CG iterations
            mv = self.matvec(w)
            cp.subtract(mv, shift * w, out=mv)
            w = mv.copy()  # This is a simplification; in practice use CG solver
            norm = cp.linalg.norm(w)
            if norm < 1e-10:
                break
            cp.divide(w, norm, out=w)
            # Compute Rayleigh quotient
            mv = self.matvec(w)
            lambda_min = min(lambda_min, float(cp.real(cp.vdot(w, mv))))
        # Power iteration for largest eigenvalue
        w = self.initialize_random_vector(self.buffers['temp'])
        lambda_max = 0
        for _ in range(num_samples):
            w = self.matvec(w)
            norm = cp.linalg.norm(w)
            if norm < 1e-10:
                break
            cp.divide(w, norm, out=w)
            lambda_max = max(lambda_max, float(
                cp.real(cp.vdot(w, self.matvec(w)))))
        return lambda_min * 0.95, lambda_max * 1.05

    def chebyshev_filter(self, src, alpha, beta):
        """Modified Chebyshev filter to emphasize smallest eigenvalues"""
        buffers = self.buffers
        t_prev = buffers['temp']
        cp.copyto(t_prev, src)
        t_curr = buffers['w']
        # Modified coefficients to target small eigenvalues
        c = (beta + alpha) / 2
        e = (beta - alpha) / 2
        # First iteration
        mv_result = self.matvec(src)
        cp.subtract(mv_result, c * src, out=t_curr)
        cp.divide(t_curr, e, out=t_curr)
        for _ in range(1, self.degree):
            cp.copyto(t_prev, t_curr)
            t_next = buffers['v']
            mv_result = self.matvec(t_curr)
            cp.subtract(mv_result, c * t_curr, out=t_curr)
            cp.divide(t_curr, e, out=t_curr)
            cp.subtract(2*t_curr, t_prev, out=t_next)
            norm = float(cp.sqrt(cp.real(cp.vdot(t_next, t_next))))
            if norm > 1e-14:
                cp.divide(t_next, norm, out=t_next)
            cp.copyto(t_curr, t_next)
        return t_curr

    def orthogonalize(self, v, eigenvectors):
        if not eigenvectors:
            norm = cp.linalg.norm(v)
            if norm > 0:
                cp.divide(v, norm, out=v)
            return v
        projection = self.buffers['projection']
        projection.fill(0)
        chunk_size = 20
        for i in range(0, len(eigenvectors), chunk_size):
            chunk = eigenvectors[i:i+chunk_size]
            Q = cp.column_stack(chunk)
            chunk_proj = Q @ (Q.conj().T @ v)
            cp.add(projection, chunk_proj, out=projection)
            del Q, chunk_proj
            self.memory_pool.free_all_blocks()
        cp.subtract(v, projection, out=v)
        norm = cp.linalg.norm(v)
        if norm > 0:
            cp.divide(v, norm, out=v)
        return v

    def solve(self):
        eigenvalues = []
        eigenvectors = []
        # Initial spectral range estimation
        # alpha, beta = self.estimate_spectral_range()
        alpha, beta = self.min_eigen_value, self.max_eigen_value
        for eigen_index in range(self.k):
            t0 = perf_counter()
            v = self.buffers['v']
            if eigen_index == 0:
                self.initialize_random_vector(v)
            else:
                # Initialize with previous eigenvectors plus perturbation
                cp.copyto(v, cp.zeros_like(v))
                for i in range(max(0, eigen_index-2), eigen_index):
                    rand_coeff = complex(cp.random.randn(), cp.random.randn())
                    cp.add(v, rand_coeff * eigenvectors[i], out=v)
                perturbation = self.buffers['temp']
                self.initialize_random_vector(perturbation)
                cp.add(v, 0.1 * perturbation, out=v)
                cp.divide(v, cp.linalg.norm(v), out=v)
            self.orthogonalize(v, eigenvectors)
            lambda_prev = float('inf')
            last_improvement = float('inf')
            for iter in range(self.max_iter):
                w = self.chebyshev_filter(v, alpha, beta)
                self.orthogonalize(w, eigenvectors)
                # Compute Rayleigh quotient
                lambda_curr = float(cp.real(cp.vdot(w, self.matvec(w))))
                rel_tol = abs(lambda_curr - lambda_prev) / abs(lambda_curr)
                if rel_tol < last_improvement:
                    last_improvement = rel_tol
                print(f"eigen_index: {eigen_index}, iter: {iter}, alpha: {alpha:.9f}, "
                      f"beta: {beta:.9f}, tol: {rel_tol:.6e}, lambda: {lambda_curr:.9f}, "
                      f"degree: {self.degree}")
                if rel_tol < self.tol:
                    break
                cp.copyto(v, w)
                lambda_prev = lambda_curr
                # Adaptive updates
                if iter % 5 == 0:
                    if rel_tol > 0.1:
                        self.degree = min(self.max_degree, int(
                            self.degree * self.growth_factor))
                    elif rel_tol < 0.01:
                        self.degree = max(self.min_degree, int(
                            self.degree * self.shrink_factor))
                    # Update bounds to focus on remaining small eigenvalues
                    alpha = max(alpha, lambda_curr * 0.5)
            beta = alpha * 2.0
            # Sort eigenvalues and eigenvectors
            eigenvalues.append(lambda_curr)
            eigenvectors.append(w.copy())
            print(
                f"eigen_index: {eigen_index}, time: {perf_counter()-t0:.2f}s")
        return cp.array(eigenvalues), cp.array(eigenvectors)

In [6]:
eigen_solver = EigenSolver()
eigenvalues, eigenvectors = eigen_solver.solve()

eigen_index: 0, iter: 0, alpha: 0.000000000, beta: 1.000000000, tol: inf, lambda: 1.485820532, degree: 10
eigen_index: 0, iter: 1, alpha: 0.742910266, beta: 1.000000000, tol: 4.026357e+01, lambda: 0.036008049, degree: 15
eigen_index: 0, iter: 2, alpha: 0.742910266, beta: 1.000000000, tol: 7.689613e-01, lambda: 0.020355476, degree: 15
eigen_index: 0, iter: 3, alpha: 0.742910266, beta: 1.000000000, tol: 3.694305e-01, lambda: 0.014864190, degree: 15
eigen_index: 0, iter: 4, alpha: 0.742910266, beta: 1.000000000, tol: 3.011464e-01, lambda: 0.011423918, degree: 15
eigen_index: 0, iter: 5, alpha: 0.742910266, beta: 1.000000000, tol: 2.757523e-01, lambda: 0.008954653, degree: 15
eigen_index: 0, iter: 6, alpha: 0.742910266, beta: 1.000000000, tol: 4.149517e-01, lambda: 0.006328593, degree: 22
eigen_index: 0, iter: 7, alpha: 0.742910266, beta: 1.000000000, tol: 4.103376e-01, lambda: 0.004487289, degree: 22
eigen_index: 0, iter: 8, alpha: 0.742910266, beta: 1.000000000, tol: 3.997986e-01, lambda

In [7]:
eigenvalues

array([0.00064586, 0.00064592, 0.00064613, 0.00064653, 0.00064607,
       0.00064632, 0.00064656, 0.00064584, 0.00064627, 0.00064609,
       0.00064595, 0.00064632, 0.01014083, 0.01013558, 0.010138  ,
       0.01014464, 0.01014965, 0.01013434, 0.01014497, 0.01013986,
       0.01015171, 0.01014499, 0.01015147, 0.01014028])

In [8]:
eigenvectors

array([[-3.84075654e-04-2.66651419e-04j, -3.36928497e-04-3.02887085e-04j,
        -3.21334373e-04-3.41950450e-04j, ...,
        -6.27122645e-05+2.22312243e-04j, -5.06123324e-05+2.10321698e-04j,
        -4.92902363e-05+2.23581243e-04j],
       [-7.71070700e-05-1.52091001e-04j, -7.70671468e-05-1.30359331e-04j,
        -7.64510478e-05-1.37932351e-04j, ...,
         3.26652575e-04-1.93951259e-04j,  3.09295458e-04-1.56527924e-04j,
         2.35338754e-04-2.18841131e-04j],
       [-2.98497034e-04-2.40727502e-04j, -2.32874852e-04-3.20330175e-04j,
        -2.29672500e-04-3.09181080e-04j, ...,
         3.48734902e-05+1.27626496e-04j,  5.83366818e-05+8.82629101e-05j,
         7.65147997e-05+8.96947458e-05j],
       ...,
       [-6.54697487e-06-3.06995789e-04j,  6.41651277e-05-2.43165647e-04j,
         1.11198045e-04-1.43879268e-04j, ...,
         1.53370071e-04-3.25092742e-06j,  1.58322931e-04-4.32864836e-05j,
         1.08713924e-04-8.65201437e-05j],
       [-6.98656868e-06-3.44644395e-05j,  6.

In [9]:
eigen_solver.matvec(eigenvectors[0])

array([-2.4846850e-07-1.7232696e-07j, -2.1796222e-07-1.9520803e-07j,
       -2.0806783e-07-2.1967207e-07j, ..., -3.9522831e-08+1.4377747e-07j,
       -3.1859145e-08+1.3590852e-07j, -3.1354915e-08+1.4408579e-07j],
      dtype=complex64)

In [10]:
eigenvectors[0]*eigenvalues[0]

array([-2.48058782e-07-1.72219263e-07j, -2.17608358e-07-1.95622400e-07j,
       -2.07536751e-07-2.20851833e-07j, ...,
       -4.05032909e-08+1.43582400e-07j, -3.26884389e-08+1.35838196e-07j,
       -3.18345510e-08+1.44401995e-07j])

In [11]:
# Verify results
print("Computed eigenvalues:")
for i, ev in enumerate(eigenvalues):
    print(f"λ_{i} = {ev:.8f}")
    # Verify eigenvector
    v = eigenvectors[i]
    w = cp.zeros_like(v)
    w = eigen_solver.matvec(v)
    error = cp.linalg.norm(w - ev * v) / cp.linalg.norm(w)
    print(f"Relative error: {error:.2e}")
    j = i+1
    if j == len(eigenvalues):
        j = 0
    print(
        f"Diff between λ_{i} and λ_{j}: {cp.linalg.norm(eigenvectors[i] - eigenvectors[j])/cp.linalg.norm(eigenvectors[i]):.2e}")

Computed eigenvalues:
λ_0 = 0.00064586
Relative error: 8.04e-03
Diff between λ_0 and λ_1: 1.41e+00
λ_1 = 0.00064592
Relative error: 9.88e-03
Diff between λ_1 and λ_2: 1.41e+00
λ_2 = 0.00064613
Relative error: 9.68e-03
Diff between λ_2 and λ_3: 1.41e+00
λ_3 = 0.00064653
Relative error: 1.02e-02
Diff between λ_3 and λ_4: 1.41e+00
λ_4 = 0.00064607
Relative error: 1.06e-02
Diff between λ_4 and λ_5: 1.41e+00
λ_5 = 0.00064632
Relative error: 1.00e-02
Diff between λ_5 and λ_6: 1.41e+00
λ_6 = 0.00064656
Relative error: 9.64e-03
Diff between λ_6 and λ_7: 1.41e+00
λ_7 = 0.00064584
Relative error: 9.99e-03
Diff between λ_7 and λ_8: 1.41e+00
λ_8 = 0.00064627
Relative error: 9.95e-03
Diff between λ_8 and λ_9: 1.41e+00
λ_9 = 0.00064609
Relative error: 1.04e-02
Diff between λ_9 and λ_10: 1.41e+00
λ_10 = 0.00064595
Relative error: 9.72e-03
Diff between λ_10 and λ_11: 1.41e+00
λ_11 = 0.00064632
Relative error: 1.01e-02
Diff between λ_11 and λ_12: 1.41e+00
λ_12 = 0.01014083
Relative error: 6.15e-03
Diff

In [19]:
eigenvalues.tofile("eigenvalues-dev33.bin")
eigenvectors.tofile("eigenvectors-dev33.bin")

In [12]:
# qcu.applyEndQcu(set_ptrs, params)